## Imports

In [1]:
import gymnasium as gym
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy
import os
import warnings

warnings.simplefilter("ignore", category=UserWarning)

## Environment

In [10]:
env = gym.make("BipedalWalker-v3", hardcore=True, render_mode="human")

In [11]:
env.reset()

(array([ 2.7473280e-03, -2.2396518e-05,  1.7422227e-03, -1.5999850e-02,
         9.1842324e-02, -2.2991430e-03,  8.6033690e-01,  3.1016136e-03,
         1.0000000e+00,  3.2247629e-02, -2.2989837e-03,  8.5388684e-01,
         1.6259747e-03,  1.0000000e+00,  4.4081411e-01,  4.4582021e-01,
         4.6142289e-01,  4.8955029e-01,  5.3410292e-01,  6.0246116e-01,
         7.0914906e-01,  8.8593203e-01,  1.0000000e+00,  1.0000000e+00],
       dtype=float32),
 {})

In [12]:
env.action_space

Box(-1.0, 1.0, (4,), float32)

In [13]:
env.observation_space

Box([-3.1415927 -5.        -5.        -5.        -3.1415927 -5.
 -3.1415927 -5.        -0.        -3.1415927 -5.        -3.1415927
 -5.        -0.        -1.        -1.        -1.        -1.
 -1.        -1.        -1.        -1.        -1.        -1.       ], [3.1415927 5.        5.        5.        3.1415927 5.        3.1415927
 5.        5.        3.1415927 5.        3.1415927 5.        5.
 1.        1.        1.        1.        1.        1.        1.
 1.        1.        1.       ], (24,), float32)

In [14]:
env.render()

In [15]:
episodes = 5
for i in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0

    while not done:
        env.render()
        action = env.action_space.sample()
        obs, obs2, reward, done, info = env.step(action)
        score += reward
    print(f"Episode: {i} Score: {score}")

env.close()

Episode: 1 Score: 1551
Episode: 2 Score: 1552
Episode: 3 Score: 1531
Episode: 4 Score: 1546
Episode: 5 Score: 1486


## Train Model

In [20]:
env = gym.make("BipedalWalker-v3", hardcore=True, render_mode="human")
env = DummyVecEnv([lambda: env])

In [23]:
log_path = os.path.join("Training", "logs")
model = PPO("MlpPolicy", env, verbose=1, tensorboard_log = log_path)

Using cpu device


In [26]:
model.learn(total_timesteps=10000000)

Logging to Training/logs/PPO_3
-----------------------------
| time/              |      |
|    fps             | 46   |
|    iterations      | 1    |
|    time_elapsed    | 44   |
|    total_timesteps | 2048 |
-----------------------------
------------------------------------------
| time/                   |              |
|    fps                  | 46           |
|    iterations           | 2            |
|    time_elapsed         | 87           |
|    total_timesteps      | 4096         |
| train/                  |              |
|    approx_kl            | 0.0067155613 |
|    clip_fraction        | 0.0333       |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.52        |
|    explained_variance   | 0.557        |
|    learning_rate        | 0.0003       |
|    loss                 | 64.5         |
|    n_updates            | 80           |
|    policy_gradient_loss | -0.00445     |
|    std                  | 0.962        |
|    value_loss           | 

## Save Model

In [27]:
ppo_path = os.path.join("Training", "Saved Models", "PPO_Driving_Model")

In [28]:
model.save(ppo_path)

In [29]:
del model

In [30]:
model = PPO.load(ppo_path, env)

## Test Model

In [31]:
evaluate_policy(model, env, n_eval_episodes=10, render=True)

(-18.918926563963034, 8.335106408523771)

In [34]:
episodes = 5
for i in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0

    while not done:
        env.render()
        action, _ = model.predict(obs)
        obs, reward, done, info = env.step(action)
        score += reward
    print(f"Episode: {i} Score: {score}")

env.close()

Episode: 1 Score: [-16.445728]
Episode: 2 Score: [-21.987177]
Episode: 3 Score: [-25.341368]
Episode: 4 Score: [-11.194461]
Episode: 5 Score: [-119.0935]
